Решается задача раннего детектирования сепсиса у пациентов

1) Подготовка датасета

In [69]:
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, classification_report
import hvplot.pandas

In [70]:
data = pd.read_csv("Dataset/Dataset.csv", sep=",")

In [71]:
data.head(10)

Unnamed: 0  Hour    HR  O2Sat   Temp    SBP   MAP   DBP  Resp  EtCO2  ...  \
0           0     0   NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN  ...   
1           1     1  65.0  100.0    NaN    NaN  72.0   NaN  16.5    NaN  ...   
2           2     2  78.0  100.0    NaN    NaN  42.5   NaN   NaN    NaN  ...   
3           3     3  73.0  100.0    NaN    NaN   NaN   NaN  17.0    NaN  ...   
4           4     4  70.0  100.0    NaN  129.0  74.0  69.0  14.0    NaN  ...   
5           5     5  62.0  100.0    NaN  124.0  85.0  61.0  14.0    NaN  ...   
6           6     6  61.0  100.0    NaN  101.0  75.0  58.0  14.0    NaN  ...   
7           7     7  68.0  100.0  35.78  142.0  93.5  78.0  16.0    NaN  ...   
8           8     8  71.0  100.0    NaN  121.0  74.0  91.0  14.0    NaN  ...   
9           9     9  69.0  100.0    NaN  120.0  79.0  98.0  14.0    NaN  ...   

   Fibrinogen  Platelets    Age  Gender  Unit1  Unit2  HospAdmTime  ICULOS  \
0         NaN        NaN  68.54       0    NaN    NaN        -0.02       1   
1         NaN        NaN  68.54       0    NaN    NaN        -0.02       2   
2         NaN        NaN  68.54       0    NaN    NaN        -0.02       3   
3         NaN        NaN  68.54       0    NaN    NaN        -0.02       4   
4         NaN      330.0  68.54       0    NaN    NaN        -0.02       5   
5         NaN        NaN  68.54       0    NaN    NaN        -0.02       6   
6         NaN        NaN  68.54       0    NaN    NaN        -0.02       7   
7         NaN        NaN  68.54       0    NaN    NaN        -0.02       8   
8         NaN        NaN  68.54       0    NaN    NaN        -0.02       9   
9         NaN        NaN  68.54       0    NaN    NaN        -0.02      10   

   SepsisLabel  Patient_ID  
0            0       17072  
1            0       17072  
2            0       17072  
3            0       17072  
4            0       17072  
5            0       17072  
6            0       17072  
7            0       17072  
8            0       17072  
9            0       17072  

[10 rows x 44 columns]

In [72]:
len(list(data['Patient_ID'].unique()))

40336

In [73]:
data.dtypes

Unnamed: 0            int64
Hour                  int64
HR                  float64
O2Sat               float64
Temp                float64
SBP                 float64
MAP                 float64
DBP                 float64
Resp                float64
EtCO2               float64
BaseExcess          float64
HCO3                float64
FiO2                float64
pH                  float64
PaCO2               float64
SaO2                float64
AST                 float64
BUN                 float64
Alkalinephos        float64
Calcium             float64
Chloride            float64
Creatinine          float64
Bilirubin_direct    float64
Glucose             float64
Lactate             float64
Magnesium           float64
Phosphate           float64
Potassium           float64
Bilirubin_total     float64
TroponinI           float64
Hct                 float64
Hgb                 float64
PTT                 float64
WBC                 float64
Fibrinogen          float64
Platelets           

Корреляция

In [74]:
data.drop('SepsisLabel', axis=1).corrwith(data.SepsisLabel).hvplot.barh(
    width=600, height=800,
    title="Correlation between Sepsis and Numeric Features",
    ylabel='Correlation', xlabel='Features',
)

:Bars   [index]   (0)

Пропущенные данные

In [75]:
columns_drop={'Unnamed: 0','FiO2','Unit1','Unit2'}

data = data.assign(Unit=data['Unit1'] + data['Unit2'])
data_mod = data.drop(columns=columns_drop)
data_mod.columns

Index(['Hour', 'HR', 'O2Sat', 'Temp', 'SBP', 'MAP', 'DBP', 'Resp', 'EtCO2',
       'BaseExcess', 'HCO3', 'pH', 'PaCO2', 'SaO2', 'AST', 'BUN',
       'Alkalinephos', 'Calcium', 'Chloride', 'Creatinine', 'Bilirubin_direct',
       'Glucose', 'Lactate', 'Magnesium', 'Phosphate', 'Potassium',
       'Bilirubin_total', 'TroponinI', 'Hct', 'Hgb', 'PTT', 'WBC',
       'Fibrinogen', 'Platelets', 'Age', 'Gender', 'HospAdmTime', 'ICULOS',
       'SepsisLabel', 'Patient_ID', 'Unit'],
      dtype='object')

In [76]:
data_impute = data_mod.copy()
columns_impute = list(data_impute.columns)
grouped_by_patient = data_impute.groupby('Patient_ID')
data_impute = grouped_by_patient.apply(lambda x: x.bfill().ffill())

In [77]:
data_impute.head(10)

Hour    HR  O2Sat   Temp    SBP   MAP   DBP  Resp  EtCO2  BaseExcess  ...  \
0     0  65.0  100.0  35.78  129.0  72.0  69.0  16.5    NaN         6.0  ...   
1     1  65.0  100.0  35.78  129.0  72.0  69.0  16.5    NaN         6.0  ...   
2     2  78.0  100.0  35.78  129.0  42.5  69.0  17.0    NaN         6.0  ...   
3     3  73.0  100.0  35.78  129.0  74.0  69.0  17.0    NaN         6.0  ...   
4     4  70.0  100.0  35.78  129.0  74.0  69.0  14.0    NaN         6.0  ...   
5     5  62.0  100.0  35.78  124.0  85.0  61.0  14.0    NaN         6.0  ...   
6     6  61.0  100.0  35.78  101.0  75.0  58.0  14.0    NaN         3.0  ...   
7     7  68.0  100.0  35.78  142.0  93.5  78.0  16.0    NaN         3.0  ...   
8     8  71.0  100.0  36.39  121.0  74.0  91.0  14.0    NaN         3.0  ...   
9     9  69.0  100.0  36.39  120.0  79.0  98.0  14.0    NaN         5.0  ...   

    WBC  Fibrinogen  Platelets    Age  Gender  HospAdmTime  ICULOS  \
0  11.3         NaN      330.0  68.54       0        -0.02       1   
1  11.3         NaN      330.0  68.54       0        -0.02       2   
2  11.3         NaN      330.0  68.54       0        -0.02       3   
3  11.3         NaN      330.0  68.54       0        -0.02       4   
4  11.3         NaN      330.0  68.54       0        -0.02       5   
5  11.0         NaN      303.0  68.54       0        -0.02       6   
6  11.0         NaN      303.0  68.54       0        -0.02       7   
7  11.0         NaN      303.0  68.54       0        -0.02       8   
8  11.0         NaN      303.0  68.54       0        -0.02       9   
9  11.0         NaN      303.0  68.54       0        -0.02      10   

   SepsisLabel  Patient_ID  Unit  
0            0       17072   NaN  
1            0       17072   NaN  
2            0       17072   NaN  
3            0       17072   NaN  
4            0       17072   NaN  
5            0       17072   NaN  
6            0       17072   NaN  
7            0       17072   NaN  
8            0       17072   NaN  
9            0       17072   NaN  

[10 rows x 41 columns]

In [78]:
null_values = data_impute.isnull().mean()*100
null_values = null_values.sort_values(ascending=False)
null_values

Bilirubin_direct    93.266633
EtCO2               89.938861
Fibrinogen          86.219455
TroponinI           81.905412
BaseExcess          63.709743
Lactate             63.533607
SaO2                62.980589
Alkalinephos        60.012756
Bilirubin_total     59.799447
AST                 59.567520
PaCO2               48.813691
HCO3                48.313952
pH                  47.427217
PTT                 45.201745
Chloride            44.905329
Unit                39.425078
Phosphate           24.518847
DBP                 16.701993
Calcium              9.776705
Magnesium            8.787277
WBC                  4.227456
Platelets            4.150598
Hgb                  3.963317
Hct                  3.786472
Creatinine           3.275459
BUN                  3.233583
Potassium            3.072845
Glucose              2.708783
SBP                  0.707121
Temp                 0.478672
MAP                  0.173817
Resp                 0.128784
O2Sat                0.024095
HR        

In [79]:
null_col = ['Bilirubin_direct','EtCO2','Fibrinogen','TroponinI','BaseExcess','Lactate','SaO2','Alkalinephos','Bilirubin_total','AST','PaCO2','HCO3','pH','PTT',
            'Chloride','Unit']
data_impute = data_impute .drop(columns=null_col)
data_impute.columns

Index(['Hour', 'HR', 'O2Sat', 'Temp', 'SBP', 'MAP', 'DBP', 'Resp', 'BUN',
       'Calcium', 'Creatinine', 'Glucose', 'Magnesium', 'Phosphate',
       'Potassium', 'Hct', 'Hgb', 'WBC', 'Platelets', 'Age', 'Gender',
       'HospAdmTime', 'ICULOS', 'SepsisLabel', 'Patient_ID'],
      dtype='object')

In [80]:
data_impute = data_impute.dropna()

In [81]:
data_impute.head(10)

Hour    HR  O2Sat   Temp    SBP   MAP   DBP  Resp   BUN  Calcium  ...  \
0     0  65.0  100.0  35.78  129.0  72.0  69.0  16.5  23.0      9.6  ...   
1     1  65.0  100.0  35.78  129.0  72.0  69.0  16.5  23.0      9.6  ...   
2     2  78.0  100.0  35.78  129.0  42.5  69.0  17.0  23.0      9.6  ...   
3     3  73.0  100.0  35.78  129.0  74.0  69.0  17.0  23.0      9.6  ...   
4     4  70.0  100.0  35.78  129.0  74.0  69.0  14.0  23.0      9.6  ...   
5     5  62.0  100.0  35.78  124.0  85.0  61.0  14.0  20.0      9.4  ...   
6     6  61.0  100.0  35.78  101.0  75.0  58.0  14.0  20.0      9.4  ...   
7     7  68.0  100.0  35.78  142.0  93.5  78.0  16.0  20.0      9.4  ...   
8     8  71.0  100.0  36.39  121.0  74.0  91.0  14.0  20.0      9.4  ...   
9     9  69.0  100.0  36.39  120.0  79.0  98.0  14.0  20.0      9.4  ...   

    Hct   Hgb   WBC  Platelets    Age  Gender  HospAdmTime  ICULOS  \
0  29.7   9.5  11.3      330.0  68.54       0        -0.02       1   
1  29.7   9.5  11.3      330.0  68.54       0        -0.02       2   
2  29.7   9.5  11.3      330.0  68.54       0        -0.02       3   
3  29.7   9.5  11.3      330.0  68.54       0        -0.02       4   
4  29.7   9.5  11.3      330.0  68.54       0        -0.02       5   
5  30.2  10.0  11.0      303.0  68.54       0        -0.02       6   
6  30.2  10.0  11.0      303.0  68.54       0        -0.02       7   
7  30.2  10.0  11.0      303.0  68.54       0        -0.02       8   
8  30.2  10.0  11.0      303.0  68.54       0        -0.02       9   
9  30.2  10.0  11.0      303.0  68.54       0        -0.02      10   

   SepsisLabel  Patient_ID  
0            0       17072  
1            0       17072  
2            0       17072  
3            0       17072  
4            0       17072  
5            0       17072  
6            0       17072  
7            0       17072  
8            0       17072  
9            0       17072  

[10 rows x 25 columns]

2) Нормализация

---


In [82]:
majority_class = data_impute[data_impute['SepsisLabel'] == 0]
minority_class = data_impute[data_impute['SepsisLabel'] == 1]
print('number of sepsis label 0 is {}'.format(len(majority_class)))
print('number of sepsis label 1 is {}'.format(len(minority_class)))

number of sepsis label 0 is 883773
number of sepsis label 1 is 18272


In [83]:
majority_class_subset = majority_class.sample(n=len(minority_class))
data_impute = pd.concat([majority_class_subset, minority_class])

In [84]:
x = data_impute.drop('SepsisLabel', axis=1)
y = data_impute['SepsisLabel']
x_train, x_test, y_train, y_test = train_test_split(x,
                                                    y,
                                                    shuffle=None,
                                                    test_size=0.2)

3) Модель

DecisionTreeClassifier

---


In [85]:
from sklearn import tree
seed = 42
model_DecTree = tree.DecisionTreeClassifier(random_state = seed,max_depth=50)
model_DecTree.fit(x_train, y_train)
pred = model_DecTree.predict(x_test)

In [86]:
plt.figure(figsize=(100,100))
tree.plot_tree(model_DecTree,
                   feature_names=x_train.columns,
                   class_names=["not sepsis", "sepsis"],
                   filled=True)

[Text(0.6568106088515705, 0.984375, 'ICULOS <= 52.5\ngini = 0.5\nsamples = 29235\nvalue = [14658, 14577]\nclass = not sepsis'),
 Text(0.4553576798262701, 0.953125, 'Temp <= 37.71\ngini = 0.46\nsamples = 20706\nvalue = [13266, 7440]\nclass = not sepsis'),
 Text(0.2888123938992464, 0.921875, 'Creatinine <= 1.195\ngini = 0.428\nsamples = 17011\nvalue = [11732, 5279]\nclass = not sepsis'),
 Text(0.1412145133094185, 0.890625, 'HospAdmTime <= -0.955\ngini = 0.367\nsamples = 10442\nvalue = [7917, 2525]\nclass = not sepsis'),
 Text(0.06730110939689862, 0.859375, 'Calcium <= 7.45\ngini = 0.312\nsamples = 6692\nvalue = [5396, 1296]\nclass = not sepsis'),
 Text(0.026234884942848674, 0.828125, 'Potassium <= 3.925\ngini = 0.46\nsamples = 867\nvalue = [556, 311]\nclass = not sepsis'),
 Text(0.019257096418201884, 0.796875, 'Resp <= 22.75\ngini = 0.497\nsamples = 476\nvalue = [255, 221]\nclass = not sepsis'),
 Text(0.013381063976394058, 0.765625, 'DBP <= 61.75\ngini = 0.485\nsamples = 396\nvalue = [23

In [87]:
print(classification_report(y_train, model_DecTree.predict(x_train)))

              precision    recall  f1-score   support

           0       1.00      1.00      1.00     14658
           1       1.00      1.00      1.00     14577

    accuracy                           1.00     29235
   macro avg       1.00      1.00      1.00     29235
weighted avg       1.00      1.00      1.00     29235



In [88]:
print(classification_report(y_test, pred))

              precision    recall  f1-score   support

           0       0.92      0.84      0.88      3614
           1       0.86      0.93      0.89      3695

    accuracy                           0.88      7309
   macro avg       0.89      0.88      0.88      7309
weighted avg       0.89      0.88      0.88      7309



GradientBoostingClassifier

---



In [89]:
from sklearn.ensemble import GradientBoostingClassifier
model_GradBoost = GradientBoostingClassifier(random_state = seed, max_depth=20)
model_GradBoost.fit(x_train, y_train)
pred = model_GradBoost.predict(x_test)

In [90]:
importance = dict(zip(x_train.columns, model_GradBoost.feature_importances_))
importance

{'Hour': 0.02051272928588456,
 'HR': 0.029425042408365607,
 'O2Sat': 0.009620777122922461,
 'Temp': 0.06950950747347413,
 'SBP': 0.015163802694035017,
 'MAP': 0.010496789518774332,
 'DBP': 0.019506459199579905,
 'Resp': 0.018312288010851482,
 'BUN': 0.028420254130047066,
 'Calcium': 0.04553081172832855,
 'Creatinine': 0.04867570028177111,
 'Glucose': 0.03829594179097805,
 'Magnesium': 0.02768114586054732,
 'Phosphate': 0.04071672424400608,
 'Potassium': 0.03269876758865456,
 'Hct': 0.027159909823933726,
 'Hgb': 0.029366208251837445,
 'WBC': 0.06246448053543958,
 'Platelets': 0.051317206785479,
 'Age': 0.04812174667677127,
 'Gender': 0.0034375037026591537,
 'HospAdmTime': 0.055054730357982265,
 'ICULOS': 0.21060848493677056,
 'Patient_ID': 0.05790298759090681}

In [91]:
print(classification_report(y_train, model_GradBoost.predict(x_train)))

              precision    recall  f1-score   support

           0       1.00      1.00      1.00     14658
           1       1.00      1.00      1.00     14577

    accuracy                           1.00     29235
   macro avg       1.00      1.00      1.00     29235
weighted avg       1.00      1.00      1.00     29235



In [92]:
print(classification_report(y_test, pred))

              precision    recall  f1-score   support

           0       0.95      0.89      0.92      3614
           1       0.90      0.96      0.93      3695

    accuracy                           0.92      7309
   macro avg       0.93      0.92      0.92      7309
weighted avg       0.93      0.92      0.92      7309



KNeighborsClassifier

---

In [93]:
from sklearn.neighbors import KNeighborsClassifier
model = KNeighborsClassifier()
model.fit(x_train, y_train)
pred = model.predict(x_test)

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


In [94]:
print(classification_report(y_train, model.predict(x_train)))

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


              precision    recall  f1-score   support

           0       1.00      0.85      0.92     14658
           1       0.87      1.00      0.93     14577

    accuracy                           0.92     29235
   macro avg       0.93      0.92      0.92     29235
weighted avg       0.93      0.92      0.92     29235



In [95]:
print(classification_report(y_test, pred))

              precision    recall  f1-score   support

           0       0.99      0.77      0.87      3614
           1       0.82      0.99      0.90      3695

    accuracy                           0.88      7309
   macro avg       0.90      0.88      0.88      7309
weighted avg       0.90      0.88      0.88      7309

